In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# imporn.cluster import KMeans
from sklearn.cluster import KMeans 
from sklearn.datasets.samples_generator import make_blobs
#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
CLIENT_ID = 'ZJTY0OS5I0ACBIWT403O12KFP0BGUS2G4PADGGWU3DR2RQWI' # your Foursquare ID
CLIENT_SECRET = 'W4MYFHNTJNT4QIKUYMVAH5QC1GYFXVZUISX21GTMAS12A14N' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)
LIMIT = 50 # limit of number of venues returned by Foursquare API
radius = 500 # define radius


Your credentails:
CLIENT_ID: ZJTY0OS5I0ACBIWT403O12KFP0BGUS2G4PADGGWU3DR2RQWI
CLIENT_SECRET:W4MYFHNTJNT4QIKUYMVAH5QC1GYFXVZUISX21GTMAS12A14N


In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [6]:
neighborhoods_data = newyork_data['features']

In [7]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [8]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [9]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [10]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [11]:
neighborhoods

Borough               Neighborhood   Latitude  Longitude
0            Bronx                  Wakefield  40.894705 -73.847201
1            Bronx                 Co-op City  40.874294 -73.829939
2            Bronx                Eastchester  40.887556 -73.827806
3            Bronx                  Fieldston  40.895437 -73.905643
4            Bronx                  Riverdale  40.890834 -73.912585
5            Bronx                Kingsbridge  40.881687 -73.902818
6        Manhattan                Marble Hill  40.876551 -73.910660
7            Bronx                   Woodlawn  40.898273 -73.867315
8            Bronx                    Norwood  40.877224 -73.879391
9            Bronx             Williamsbridge  40.881039 -73.857446
10           Bronx                 Baychester  40.866858 -73.835798
11           Bronx             Pelham Parkway  40.857413 -73.854756
12           Bronx                City Island  40.847247 -73.786488
13           Bronx               Bedford Park  40.870185 -73.885512
14           Bronx         University Heights  40.855727 -73.910416
15           Bronx             Morris Heights  40.847898 -73.919672
16           Bronx                    Fordham  40.860997 -73.896427
17           Bronx               East Tremont  40.842696 -73.887356
18           Bronx                 West Farms  40.839475 -73.877745
19           Bronx               High  Bridge  40.836623 -73.926102
20           Bronx                    Melrose  40.819754 -73.909422
21           Bronx                 Mott Haven  40.806239 -73.916100
22           Bronx                Port Morris  40.801664 -73.913221
23           Bronx                   Longwood  40.815099 -73.895788
24           Bronx                Hunts Point  40.809730 -73.883315
25           Bronx                 Morrisania  40.823592 -73.901506
26           Bronx                  Soundview  40.821012 -73.865746
27           Bronx               Clason Point  40.806551 -73.854144
28           Bronx                Throgs Neck  40.815109 -73.816350
29           Bronx               Country Club  40.844246 -73.824099
30           Bronx                Parkchester  40.837938 -73.856003
31           Bronx         Westchester Square  40.840619 -73.842194
32           Bronx                   Van Nest  40.843608 -73.866299
33           Bronx                Morris Park  40.847549 -73.850402
34           Bronx                    Belmont  40.857277 -73.888452
35           Bronx             Spuyten Duyvil  40.881395 -73.917190
36           Bronx            North Riverdale  40.908543 -73.904531
37           Bronx                 Pelham Bay  40.850641 -73.832074
38           Bronx              Schuylerville  40.826580 -73.826203
39           Bronx             Edgewater Park  40.821986 -73.813885
40           Bronx                Castle Hill  40.819014 -73.848027
41           Bronx                  Olinville  40.871371 -73.863324
42           Bronx             Pelham Gardens  40.862966 -73.841612
43           Bronx                  Concourse  40.834284 -73.915589
44           Bronx                  Unionport  40.829774 -73.850535
45           Bronx                   Edenwald  40.884561 -73.848083
46        Brooklyn                  Bay Ridge  40.625801 -74.030621
47        Brooklyn                Bensonhurst  40.611009 -73.995180
48        Brooklyn                Sunset Park  40.645103 -74.010316
49        Brooklyn                 Greenpoint  40.730201 -73.954241
50        Brooklyn                  Gravesend  40.595260 -73.973471
51        Brooklyn             Brighton Beach  40.576825 -73.965094
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438
54        Brooklyn                   Flatbush  40.636326 -73.958401
55        Brooklyn              Crown Heights  40.670829 -73.943291
56        Brooklyn              East Flatbush  40.641718 -73.936103
57        Brooklyn                 Kensington  40.642382 -73.980421

In [12]:
print('The dataframe encompasses {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe encompasses 5 boroughs and 306 neighborhoods.


In [13]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [14]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [15]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In [16]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
neighborhood_latitude = location.latitude
neighborhood_longitude = location.longitude
print('The geograpical coordinates of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Manhattan are 40.7127281, -74.0060152.


In [17]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

In [18]:
# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=ZJTY0OS5I0ACBIWT403O12KFP0BGUS2G4PADGGWU3DR2RQWI&client_secret=W4MYFHNTJNT4QIKUYMVAH5QC1GYFXVZUISX21GTMAS12A14N&v=20180605&ll=40.87655077879964,-73.91065965862981&radius=500&limit=50'

In [19]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e9fe8376001fe001ca05c97'},
 'response': {'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 25,
  'suggestedBounds': {'ne': {'lat': 40.88105078329964,
    'lng': -73.90471933917806},
   'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b4429abf964a52037f225e3',
       'name': "Arturo's",
       'location': {'address': '5198 Broadway',
        'crossStreet': 'at 225th St.',
        'lat': 40.87441177110231,
        'lng': -73.91027100981574,
        'labeledLatLngs': [{'label': 'display',
          'lat': 40.87441177110231,
          'lng': -73.91027100981574},
         {'label': 

In [20]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [21]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name   categories        lat        lng
0       Arturo's  Pizza Place  40.874412 -73.910271
1    Bikram Yoga  Yoga Studio  40.876844 -73.906204
2  Tibbett Diner        Diner  40.880404 -73.908937
3        Dunkin'   Donut Shop  40.877136 -73.906666
4      Starbucks  Coffee Shop  40.877531 -73.905582

In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [23]:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [24]:
print(manhattan_venues.shape)
manhattan_venues.head()

(1868, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066        Dunkin'   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877136       -73.906666     Donut Shop  
4       40.877531       -73.905582    Coffee Shop

In [25]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       50                      50     50   
Carnegie Hill                           50                      50     50   
Central Harlem                          45                      45     45   
Chelsea                                 50                      50     50   
Chinatown                               50                      50     50   
Civic Center                            50                      50     50   
Clinton                                 50                      50     50   
East Harlem                             43                      43     43   
East Village                            50                      50     50   
Financial District                      50                      50     50   
Flatiron                                50                      50     50   
Gramercy                                50                      50     50   
Greenwich Village                       50                      50     50   
Hamilton Heights                        50                      50     50   
Hudson Yards                            50                      50     50   
Inwood                                  50                      50     50   
Lenox Hill                              50                      50     50   
Lincoln Square                          50                      50     50   
Little Italy                            50                      50     50   
Lower East Side                         44                      44     44   
Manhattan Valley                        34                      34     34   
Manhattanville                          47                      47     47   
Marble Hill                             25                      25     25   
Midtown                                 50                      50     50   
Midtown South                           50                      50     50   
Morningside Heights                     39                      39     39   
Murray Hill                             50                      50     50   
Noho                                    50                      50     50   
Roosevelt Island                        27                      27     27   
Soho                                    50                      50     50   
Stuyvesant Town                         14                      14     14   
Sutton Place                            50                      50     50   
Tribeca                                 50                      50     50   
Tudor City                              50                      50     50   
Turtle Bay                              50                      50     50   
Upper East Side                         50                      50     50   
Upper West Side                         50                      50     50   
Washington Heights                      50                      50     50   
West Village                            50                      50     50   
Yorkville                               50                      50     50   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                50               50              50  
Carnegie Hill                    50               50              50  
Central Harlem                   45               45              45  
Chelsea                          50               50              50  
Chinatown                        50               50              50  
Civic Center                     50               50              50  
Clinton                          50               50              50  
East Harlem                      43               43              43  
East Village                     50               50              50  
Finan

In [26]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  African Restaurant  \
0  Marble Hill                  0               0                   0   
1  Marble Hill                  0               0                   0   
2  Marble Hill                  0               0                   0   
3  Marble Hill                  0               0                   0   
4  Marble Hill                  0               0                   0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0                    0             0       0                 0   
1                    0             0       0                 0   
2                    0             0       0                 0   
3                    0             0       0                 0   
4                    0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                    0          0           0           0       0     0    0   
1                    0          0           0           0       0     0    0   
2                    0          0           0           0       0     0    0   
3                    0          0           0           0       0     0    0   
4                    0          0           0           0       0     0    0   

   Baseball Field  Beer Bar  Beer Garden  Beer Store  \
0               0         0            0           0   
1               0         0            0           0   
2               0         0            0           0   
3               0         0            0           0   
4               0         0            0           0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Breakfast Spot  \
0              0          0         0           0               0   
1              0          0         0           0               0   
2              0          0         0           0               0   
3              0          0         0           0               0   
4              0          0         0           0               0   

   Bridal Shop  Bridge  Bubble Tea Shop  Building  Burger Joint  \
0            0       0                0         0             0   
1            0       0                0         0             0   
2            0       0                0         0             0   
3            0       0                0         0             0   
4            0       0                0         0             0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Butcher  Cafeteria  Café  \
0              0         0            0         0        0          0     0   
1      

In [27]:
manhattan_onehot.shape

(1868, 282)

In [28]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0     Battery Park City               0.00            0.00   
1         Carnegie Hill               0.00            0.00   
2        Central Harlem               0.00            0.00   
3               Chelsea               0.00            0.00   
4             Chinatown               0.00            0.00   
5          Civic Center               0.00            0.00   
6               Clinton               0.00            0.00   
7           East Harlem               0.00            0.00   
8          East Village               0.00            0.00   
9    Financial District               0.00            0.00   
10             Flatiron               0.00            0.00   
11             Gramercy               0.00            0.00   
12    Greenwich Village               0.00            0.00   
13     Hamilton Heights               0.00            0.00   
14         Hudson Yards               0.00            0.00   
15               Inwood               0.00            0.00   
16           Lenox Hill               0.00            0.00   
17       Lincoln Square               0.00            0.00   
18         Little Italy               0.00            0.00   
19      Lower East Side               0.00            0.00   
20     Manhattan Valley               0.00            0.00   
21       Manhattanville               0.00            0.00   
22          Marble Hill               0.00            0.00   
23              Midtown               0.00            0.00   
24        Midtown South               0.00            0.00   
25  Morningside Heights               0.00            0.00   
26          Murray Hill               0.00            0.00   
27                 Noho               0.00            0.00   
28     Roosevelt Island               0.00            0.00   
29                 Soho               0.00            0.00   
30      Stuyvesant Town               0.00            0.00   
31         Sutton Place               0.00            0.02   
32              Tribeca               0.00            0.00   
33           Tudor City               0.00            0.00   
34           Turtle Bay               0.00            0.00   
35      Upper East Side               0.00            0.00   
36      Upper West Side               0.00            0.00   
37   Washington Heights               0.02            0.00   
38         West Village               0.00            0.00   
39            Yorkville               0.00            0.00   

    African Restaurant  American Restaurant  Antique Shop  Arcade  \
0             0.000000             0.000000          0.00    0.00   
1             0.000000             0.020000          0.00    0.00   
2             0.044444             0.044444          0.00    0.00   
3             0.000000             0.040000          0.00    0.00   
4             0.000000             0.060000          0.00    0.00   
5             0.000000             0.040000          0.02    0.00   
6             0.000000             0.040000          0.00    0.00   
7             0.000000             0.000000          0.00    0.00   
8             0.000000             0.020000          0.00    0.00   
9             0.000000             0.040000          0.00    0.00   
10            0.000000             0.020000          0.00    0.00   
11            0.000000             0.040000          0.00    0.02   
12            0.000000             0.000000          0.00    0.00   
13            0.000000             0.000000          0.00    0.00   
14            0.000000             0.060000          0.00    0.00   
15            0.000000             0.040000          0.00    0.00   
16            0.000000             0.000000          0.00    0.00   
17            0.000000             0.040000          0.00    0.00   
18            0.000000             0.000000          0.00    0.00   
19            0.000000             0.000000          0.00    0.00   
20            0.000

In [29]:
manhattan_grouped.shape

(40, 282)

In [30]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
           venue  freq
0           Park  0.12
1          Hotel  0.08
2            Gym  0.06
3  Memorial Site  0.06
4   Gourmet Shop  0.04


----Carnegie Hill----
                  venue  freq
0           Coffee Shop  0.08
1           Yoga Studio  0.06
2                  Café  0.06
3  Gym / Fitness Center  0.06
4             Bookstore  0.06


----Central Harlem----
                  venue  freq
0    Chinese Restaurant  0.04
1  Gym / Fitness Center  0.04
2    African Restaurant  0.04
3   American Restaurant  0.04
4                   Bar  0.04


----Chelsea----
            venue  freq
0     Coffee Shop  0.08
1  Ice Cream Shop  0.06
2    Cupcake Shop  0.04
3          Bakery  0.04
4          Market  0.04


----Chinatown----
                 venue  freq
0  American Restaurant  0.06
1   Chinese Restaurant  0.06
2         Cocktail Bar  0.04
3     Greek Restaurant  0.04
4             Boutique  0.04


----Civic Center----
                  venue  freq
0  Gym / Fitness C

In [31]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [32]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park                 Hotel   
1      Carnegie Hill           Coffee Shop  Gym / Fitness Center   
2     Central Harlem  Gym / Fitness Center    Chinese Restaurant   
3            Chelsea           Coffee Shop        Ice Cream Shop   
4          Chinatown   American Restaurant    Chinese Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Gym         Memorial Site                 Plaza   
1                  Café             Bookstore           Yoga Studio   
2                   Bar   Fried Chicken Joint     French Restaurant   
3             Bookstore                Market   American Restaurant   
4      Asian Restaurant              Boutique                   Spa   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Food Court          Burger Joint         Shopping Mall   
1           Pizza Place     French Restaurant                   Spa   
2        Cosmetics Shop    Seafood Restaurant    African Restaurant   
3                Bakery          Cupcake Shop    Italian Restaurant   
4          Noodle House          Cocktail Bar        Sandwich Place   

  9th Most Common Venue           10th Most Common Venue  
0          Gourmet Shop                        Wine Shop  
1             Wine Shop                              Gym  
2   American Restaurant  Southern / Soul Food Restaurant  
3    Seafood Restaurant                Indian Restaurant  
4        Ice Cream Shop               Salon / Barbershop

In [33]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 2, 2, 2, 2, 2, 1, 4, 2, 2], dtype=int32)

In [34]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               4   
1  Manhattan           Chinatown  40.715618 -73.994279               2   
2  Manhattan  Washington Heights  40.851903 -73.936900               4   
3  Manhattan              Inwood  40.867684 -73.921210               4   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place           Coffee Shop                   Gym   
1   American Restaurant    Chinese Restaurant      Asian Restaurant   
2                  Café         Deli / Bodega             Wine Shop   
3    Mexican Restaurant           Pizza Place                Bakery   
4                  Café           Coffee Shop         Deli / Bodega   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0           Yoga Studio    Miscellaneous Shop            Steakhouse   
1              Boutique                   Spa          Noodle House   
2                Bakery    Spanish Restaurant     Mobile Phone Shop   
3                  Café            Restaurant                  Park   
4    Mexican Restaurant           Pizza Place           Yoga Studio   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0          Supplement Shop    Seafood Restaurant            Donut Shop   
1             Cocktail Bar        Sandwich Place        Ice Cream Shop   
2  New American Restaurant                  Park      Tapas Restaurant   
3       Frozen Yogurt Shop              Wine Bar                Lounge   
4         Sushi Restaurant                Bakery  Caribbean Restaurant   

  10th Most Common Venue  
0         Tennis Stadium  
1     Salon / Barbershop  
2            Coffee Shop  
3    American Restaurant  
4           Cocktail Bar

In [36]:
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
brooklyn_data.head()

Borough Neighborhood   Latitude  Longitude
0  Brooklyn    Bay Ridge  40.625801 -74.030621
1  Brooklyn  Bensonhurst  40.611009 -73.995180
2  Brooklyn  Sunset Park  40.645103 -74.010316
3  Brooklyn   Greenpoint  40.730201 -73.954241
4  Brooklyn    Gravesend  40.595260 -73.973471

## We repeat the same process for each borough, starting with Brooklyn

In [37]:
address = 'Brooklyn, NY'

geolocator1 = Nominatim(user_agent="ny_explorer")
location1 = geolocator1.geocode(address)
latitude1 = location.latitude
longitude1 = location.longitude
print('The geograpical coordinates of Brooklyn are {}, {}.'.format(latitude1, longitude1))

The geograpical coordinates of Brooklyn are 40.7896239, -73.9598939.


In [38]:
brooklyn_venues = getNearbyVenues(names=brooklyn_data['Neighborhood'],
                                   latitudes=brooklyn_data['Latitude'],
                                   longitudes=brooklyn_data['Longitude']
                                  )

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


In [39]:
brooklyn_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Bath Beach                                    42                      42   
Bay Ridge                                     50                      50   
Bedford Stuyvesant                            28                      28   
Bensonhurst                                   33                      33   
Bergen Beach                                   6                       6   
Boerum Hill                                   50                      50   
Borough Park                                  19                      19   
Brighton Beach                                45                      45   
Broadway Junction                             14                      14   
Brooklyn Heights                              50                      50   
Brownsville                                   22                      22   
Bushwick                                      50                      50   
Canarsie                                       5                       5   
Carroll Gardens                               50                      50   
City Line                                     37                      37   
Clinton Hill                                  50                      50   
Cobble Hill                                   50                      50   
Coney Island                                  19                      19   
Crown Heights                                 20                      20   
Cypress Hills                                 29                      29   
Ditmas Park                                   43                      43   
Downtown                                      50                      50   
Dumbo                                         50                      50   
Dyker Heights                                  8                       8   
East Flatbush                                 13                      13   
East New York                                 13                      13   
East Williamsburg                             50                      50   
Erasmus                                       20                      20   
Flatbush                                      18                      18   
Flatlands                                     18                      18   
Fort Greene                                   50                      50   
Fort Hamilton                                 50                      50   
Fulton Ferry                                  50                      50   
Georgetown                                    30                      30   
Gerritsen Beach                               17                      17   
Gowanus                                       50                      50   
Gravesend                                     26                      26   
Greenpoint                                    50                      50   
Highland Park                                 14                      14   
Homecrest                                     38                      38   
Kensington                                    34                      34   
Madison                                       11                      11   
Manhattan Beach                               10                      10   
Manhattan Terrace                             27                      27   
Marine Park                                    9                       9   
Midwood                                       11                      11   
Mill Basin                                    32                      32   
Mill Island                                    2                       2   
New Lots                                      15                      15   
North Side                                    50                      50   
Ocean Hill                                    28                      28   

In [40]:
print('There are {} unique categories.'.format(len(brooklyn_venues['Venue Category'].unique())))

There are 270 unique categories.


In [41]:
# one hot encoding
brooklyn_onehot = pd.get_dummies(brooklyn_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
brooklyn_onehot['Neighborhood'] = brooklyn_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [brooklyn_onehot.columns[-1]] + list(brooklyn_onehot.columns[:-1])
brooklyn_onehot = brooklyn_onehot[fixed_columns]

brooklyn_onehot.head()

Yoga Studio  Accessories Store  Airport Terminal  American Restaurant  \
0            0                  0                 0                    0   
1            0                  0                 0                    0   
2            0                  0                 0                    0   
3            0                  0                 0                    0   
4            0                  0                 0                    0   

   Antique Shop  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0             0                 0                       0            0   
1             0                 0                       0            0   
2             0                 0                       0            0   
3             0                 0                       0            0   
4             0                 0                       0            0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                   0            0          0           0       0     0    0   
1                   0            0          0           1       0     0    0   
2                   0            0          0           0       0     0    0   
3                   0            0          0           0       0     0    0   
4                   0            0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Beach  Beer Bar  \
0               0                 0                 0      0         0   
1               0                 0                 0      0         0   
2               0                 0                 0      0         0   
3               0                 0                 0      0         0   
4               0                 0                 0      0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0            0           0              0                         0   
1            0           0              0                         0   
2            0           0              0                         0   
3            0           0              0                         0   
4            0           0              0                         0   

   Bike Shop  Board Shop  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0          0           0              0          0         0           0   
1          0           0              0          0         0           0   
2          0           0              0          0         0           0   
3          0           0              0          0         0           0   
4          0           0              0          0         0           0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Buffet  \
0               0        0            0       0                0       0   
1               0        0            0       0                0       0   
2               0        0            0       0                0       0   
3               0        0            0       0                0       0   
4               1        0            0       0                0       0   

   Burger Joint  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0             0              0         0            0         0   
1             0              0         0            0         0   
2             0              0         0            0         0   
3             0              0         0            0         0   
4             0              0         0            0         0   

   Business Service  Butcher  Café

In [42]:
brooklyn_onehot.shape

(2113, 270)

In [43]:
brooklyn_grouped = brooklyn_onehot.groupby('Neighborhood').mean().reset_index()
brooklyn_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                  Bath Beach     0.000000               0.00   
1                   Bay Ridge     0.000000               0.00   
2          Bedford Stuyvesant     0.000000               0.00   
3                 Bensonhurst     0.000000               0.00   
4                Bergen Beach     0.000000               0.00   
5                 Boerum Hill     0.040000               0.00   
6                Borough Park     0.000000               0.00   
7              Brighton Beach     0.000000               0.00   
8           Broadway Junction     0.000000               0.00   
9            Brooklyn Heights     0.080000               0.00   
10                Brownsville     0.000000               0.00   
11                   Bushwick     0.000000               0.00   
12                   Canarsie     0.000000               0.00   
13            Carroll Gardens     0.000000               0.00   
14                  City Line     0.000000               0.00   
15               Clinton Hill     0.040000               0.00   
16                Cobble Hill     0.060000               0.00   
17               Coney Island     0.000000               0.00   
18              Crown Heights     0.000000               0.00   
19              Cypress Hills     0.000000               0.00   
20                Ditmas Park     0.023256               0.00   
21                   Downtown     0.020000               0.00   
22                      Dumbo     0.040000               0.00   
23              Dyker Heights     0.000000               0.00   
24              East Flatbush     0.000000               0.00   
25              East New York     0.000000               0.00   
26          East Williamsburg     0.000000               0.00   
27                    Erasmus     0.050000               0.00   
28                   Flatbush     0.000000               0.00   
29                  Flatlands     0.000000               0.00   
30                Fort Greene     0.020000               0.00   
31              Fort Hamilton     0.000000               0.00   
32               Fulton Ferry     0.000000               0.00   
33                 Georgetown     0.000000               0.00   
34            Gerritsen Beach     0.000000               0.00   
35                    Gowanus     0.020000               0.00   
36                  Gravesend     0.000000               0.00   
37                 Greenpoint     0.060000               0.00   
38              Highland Park     0.000000               0.00   
39                  Homecrest     0.000000               0.00   
40                 Kensington     0.000000               0.00   
41                    Madison     0.000000               0.00   
42            Manhattan Beach     0.000000               0.00   
43          Manhattan Terrace     0.000000               0.00   
44                Marine Park     0.000000               0.00   
45                    Midwood     0.000000               0.00   
46                 Mill Basin     0.000000               0.00   
47                Mill Island     0.000000               0.00   
48                   New Lots     0.000000               0.00   
49                 North Side     0.040000               0.00   
50                 Ocean Hill     0.000000               0.00   
51              Ocean Parkway     0.000000               0.00   
52            Paerdegat Basin     0.000000               0.00   
53                 Park Slope     0.020000               0.02   
54           Prospect Heights     0.020000               0.00   
55  Prospect Lefferts Gardens     0.000000               0.00   
56        Prospect Park South     0.000000               0.00   
57                   Red Hook     0.000000               0.00   
58             Remsen Village     0.000000               0.00   
59                      Rugby     0.000000               0.00   
60                   Sea Gate     0.000000          

In [44]:
num_top_venues = 5

for hood in brooklyn_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = brooklyn_grouped[brooklyn_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                  venue  freq
0              Pharmacy  0.07
1    Italian Restaurant  0.05
2      Sushi Restaurant  0.05
3    Chinese Restaurant  0.05
4  Fast Food Restaurant  0.05


----Bay Ridge----
                venue  freq
0                 Spa  0.10
1  Italian Restaurant  0.08
2    Greek Restaurant  0.06
3         Pizza Place  0.06
4          Hookah Bar  0.04


----Bedford Stuyvesant----
         venue  freq
0     Bus Stop  0.07
1  Coffee Shop  0.07
2         Café  0.07
3  Pizza Place  0.07
4          Bar  0.07


----Bensonhurst----
                venue  freq
0  Chinese Restaurant  0.09
1         Pizza Place  0.06
2          Donut Shop  0.06
3  Italian Restaurant  0.06
4    Sushi Restaurant  0.06


----Bergen Beach----
                venue  freq
0     Harbor / Marina  0.33
1      Baseball Field  0.17
2  Athletics & Sports  0.17
3          Playground  0.17
4          Donut Shop  0.17


----Boerum Hill----
                    venue  freq
0                     B

In [45]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = brooklyn_grouped['Neighborhood']

for ind in np.arange(brooklyn_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(brooklyn_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach              Pharmacy           Gas Station   
1           Bay Ridge                   Spa    Italian Restaurant   
2  Bedford Stuyvesant                   Bar              Bus Stop   
3         Bensonhurst    Chinese Restaurant            Donut Shop   
4        Bergen Beach       Harbor / Marina        Baseball Field   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Fast Food Restaurant      Sushi Restaurant    Italian Restaurant   
1           Pizza Place      Greek Restaurant            Hookah Bar   
2                  Café           Pizza Place           Coffee Shop   
3        Ice Cream Shop    Italian Restaurant           Pizza Place   
4            Playground            Donut Shop    Athletics & Sports   

  6th Most Common Venue 7th Most Common Venue    8th Most Common Venue  \
0       Bubble Tea Shop           Pizza Place       Chinese Restaurant   
1            Bagel Shop        Ice Cream Shop            Grocery Store   
2              Tiki Bar   Fried Chicken Joint  Fruit & Vegetable Store   
3      Sushi Restaurant              Pharmacy             Liquor Store   
4   Filipino Restaurant    Falafel Restaurant                     Farm   

  9th Most Common Venue   10th Most Common Venue  
0    Dim Sum Restaurant      Rental Car Location  
1    Chinese Restaurant      American Restaurant  
2              Boutique  New American Restaurant  
3        Cosmetics Shop                  Factory  
4        Farmers Market     Fast Food Restaurant

In [46]:
bronx_data = neighborhoods[neighborhoods['Borough'] == 'Bronx'].reset_index(drop=True)
bronx_data.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

## Then The Bronx

In [47]:
address = 'Bronx, NY'

geolocator2 = Nominatim(user_agent="ny_explorer")
location2 = geolocator2.geocode(address)
latitude2 = location.latitude
longitude2 = location.longitude
print('The geograpical coordinate of the Bronx are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of the Bronx are 40.7127281, -74.0060152.


In [48]:
bronx_venues = getNearbyVenues(names=bronx_data['Neighborhood'],
                                   latitudes=bronx_data['Latitude'],
                                   longitudes=bronx_data['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Claremont Village
Concourse Village
Mount Eden
Mount Hope
Bronxdale
Allerton
Kingsbridge Heights


In [49]:
print(bronx_venues.shape)
bronx_venues.head()

(1124, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896528       -73.844700        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [50]:
bronx_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Allerton                                32                      32     32   
Baychester                              21                      21     21   
Bedford Park                            32                      32     32   
Belmont                                 50                      50     50   
Bronxdale                               12                      12     12   
Castle Hill                             10                      10     10   
City Island                             26                      26     26   
Claremont Village                       16                      16     16   
Clason Point                            11                      11     11   
Co-op City                              16                      16     16   
Concourse                               26                      26     26   
Concourse Village                       39                      39     39   
Country Club                             5                       5      5   
East Tremont                            20                      20     20   
Eastchester                             21                      21     21   
Edenwald                                 5                       5      5   
Edgewater Park                          24                      24     24   
Fieldston                                3                       3      3   
Fordham                                 50                      50     50   
High  Bridge                            29                      29     29   
Hunts Point                             11                      11     11   
Kingsbridge                             50                      50     50   
Kingsbridge Heights                     33                      33     33   
Longwood                                 8                       8      8   
Melrose                                 28                      28     28   
Morris Heights                          11                      11     11   
Morris Park                             22                      22     22   
Morrisania                              30                      30     30   
Mott Haven                              19                      19     19   
Mount Eden                              31                      31     31   
Mount Hope                              12                      12     12   
North Riverdale                         21                      21     21   
Norwood                                 33                      33     33   
Olinville                               11                      11     11   
Parkchester                             35                      35     35   
Pelham Bay                              36                      36     36   
Pelham Gardens                          20                      20     20   
Pelham Parkway                          23                      23     23   
Port Morris                             15                      15     15   
Riverdale                               12                      12     12   
Schuylerville                           21                      21     21   
Soundview                               16                      16     16   
Spuyten Duyvil                           8                       8      8   
Throgs Neck                             12                      12     12   
Unionport                               22                      22     22   
University Heights                      20                      20     20   
Van Nest                                23                      23     23   
Wakefield                               10                      10     10   
West Farms                              22                      22     22   
Westchester Square                      30                      30     30   
Williamsbridge   

In [51]:
print('There are {} uniques categories.'.format(len(bronx_venues['Venue Category'].unique())))

There are 162 uniques categories.


In [52]:
# one hot encoding
bronx_onehot = pd.get_dummies(bronx_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
bronx_onehot['Neighborhood'] = bronx_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [bronx_onehot.columns[-1]] + list(bronx_onehot.columns[:-1])
bronx_onehot = bronx_onehot[fixed_columns]

bronx_onehot.head()

Neighborhood  Accessories Store  African Restaurant  American Restaurant  \
0    Wakefield                  0                   0                    0   
1    Wakefield                  0                   0                    0   
2    Wakefield                  0                   0                    0   
3    Wakefield                  0                   0                    0   
4    Wakefield                  0                   0                    0   

   Arcade  Arepa Restaurant  Art Gallery  Art Museum  Asian Restaurant  \
0       0                 0            0           0                 0   
1       0                 0            0           0                 0   
2       0                 0            0           0                 0   
3       0                 0            0           0                 0   
4       0                 0            0           0                 0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Beer Bar  Boat or Ferry  Bookstore  Bowling Alley  Breakfast Spot  Brewery  \
0         0              0          0              0               0        0   
1         0              0          0              0               0        0   
2         0              0          0              0               0        0   
3         0              0          0              0               0        0   
4         0              0          0              0               0        0   

   Buffet  Building  Burger Joint  Bus Line  Bus Station  Bus Stop  Café  \
0       0         0             0         0            0         0     0   
1       0         0             0         0            0         0     0   
2       0         0             0         0            0         0     0   
3       0         0             0         0            0         0     0   
4       0         0             0         0            0         0     0   

   Candy Store  Caribbean Restaurant  Check Cashing Service  Cheese Shop  \
0            0                     0                      0            0   
1            0                     0                      0            0   
2            0                     0                      0            0   
3            0                     0                      0            0   
4            0                     0                      0            0   

   Chinese Restaurant  Clothing Store  Coffee Shop  Comfort Food Restaurant  \
0                   0               0            0                        0   
1                   0               0            0                        0   
2                   0               0            0                        0   
3                   0               0            0                        0   
4                   0               0            0                        0   

   Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0                           0                  0               0   
1                           0                  0               0   
2                           0                  0               0   
3                           0                  0               0   
4                           0                  0               0   

   Cupcake Shop  Dance Studio  Deli / Bodega  Department Store  Dessert Shop  \
0             0             0              0                 0             1   
1             0             0              0                 0             0   
2             0             0              0                 0             0

In [53]:
bronx_grouped = bronx_onehot.groupby('Neighborhood').mean().reset_index()
bronx_grouped

Neighborhood  Accessories Store  African Restaurant  \
0              Allerton               0.00            0.000000   
1            Baychester               0.00            0.000000   
2          Bedford Park               0.00            0.000000   
3               Belmont               0.00            0.000000   
4             Bronxdale               0.00            0.000000   
5           Castle Hill               0.00            0.000000   
6           City Island               0.00            0.000000   
7     Claremont Village               0.00            0.000000   
8          Clason Point               0.00            0.000000   
9            Co-op City               0.00            0.000000   
10            Concourse               0.00            0.038462   
11    Concourse Village               0.00            0.000000   
12         Country Club               0.00            0.000000   
13         East Tremont               0.00            0.000000   
14          Eastchester               0.00            0.000000   
15             Edenwald               0.00            0.000000   
16       Edgewater Park               0.00            0.000000   
17            Fieldston               0.00            0.000000   
18              Fordham               0.02            0.020000   
19         High  Bridge               0.00            0.000000   
20          Hunts Point               0.00            0.000000   
21          Kingsbridge               0.00            0.000000   
22  Kingsbridge Heights               0.00            0.000000   
23             Longwood               0.00            0.000000   
24              Melrose               0.00            0.000000   
25       Morris Heights               0.00            0.000000   
26          Morris Park               0.00            0.000000   
27           Morrisania               0.00            0.000000   
28           Mott Haven               0.00            0.000000   
29           Mount Eden               0.00            0.000000   
30           Mount Hope               0.00            0.000000   
31      North Riverdale               0.00            0.000000   
32              Norwood               0.00            0.000000   
33            Olinville               0.00            0.000000   
34          Parkchester               0.00            0.000000   
35           Pelham Bay               0.00            0.000000   
36       Pelham Gardens               0.00            0.000000   
37       Pelham Parkway               0.00            0.000000   
38          Port Morris               0.00            0.000000   
39            Riverdale               0.00            0.000000   
40        Schuylerville               0.00            0.000000   
41            Soundview               0.00            0.000000   
42       Spuyten Duyvil               0.00            0.000000   
43          Throgs Neck               0.00            0.000000   
44            Unionport               0.00            0.000000   
45   University Heights               0.00            0.050000   
46             Van Nest               0.00            0.000000   
47            Wakefield               0.00            0.000000   
48           West Farms               0.00            0.000000   
49   Westchester Square               0.00            0.000000   
50       Williamsbridge               0.00            0.000000   
51             Woodlawn               0.00            0.000000   

    American Restaurant    Arcade  Arepa Restaurant  Art Gallery  Art Museum  \
0              0.031250  0.000000          0.000000     0.000000    0.000000   
1              0.000000  0.047619          0.000000     0.000000    0.000000   
2              0.000000  0.000000          0.000000     0.000000    0.000000   
3              0.020000  0.000000          0.000000     0.000000    0.000000   
4              0.000000  0.000000          0.000000     0.000000    0.000000   
5              0.000000  0.00000

In [54]:
num_top_venues = 5

for hood in bronx_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = bronx_grouped[bronx_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0         Pizza Place  0.12
1       Deli / Bodega  0.09
2         Bus Station  0.06
3    Department Store  0.06
4  Chinese Restaurant  0.06


----Baychester----
                 venue  freq
0           Donut Shop  0.10
1       Discount Store  0.05
2       Sandwich Place  0.05
3   Spanish Restaurant  0.05
4  Fried Chicken Joint  0.05


----Bedford Park----
                venue  freq
0               Diner  0.12
1       Deli / Bodega  0.09
2         Pizza Place  0.09
3  Mexican Restaurant  0.06
4  Chinese Restaurant  0.06


----Belmont----
                venue  freq
0  Italian Restaurant  0.32
1         Pizza Place  0.12
2       Deli / Bodega  0.10
3              Bakery  0.08
4        Dessert Shop  0.06


----Bronxdale----
                   venue  freq
0     Italian Restaurant  0.08
1  Performing Arts Venue  0.08
2            Supermarket  0.08
3         Breakfast Spot  0.08
4     Mexican Restaurant  0.08


----Castle Hill----
            ven

In [55]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = bronx_grouped['Neighborhood']

for ind in np.arange(bronx_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(bronx_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood   1st Most Common Venue      2nd Most Common Venue  \
0              Allerton             Pizza Place              Deli / Bodega   
1            Baychester              Donut Shop         Spanish Restaurant   
2          Bedford Park                   Diner              Deli / Bodega   
3               Belmont      Italian Restaurant                Pizza Place   
4             Bronxdale                    Bank         Spanish Restaurant   
5           Castle Hill           Deli / Bodega                      Diner   
6           City Island         Harbor / Marina         Seafood Restaurant   
7     Claremont Village                  Bakery              Grocery Store   
8          Clason Point                    Park                       Pool   
9            Co-op City          Baseball Field                Bus Station   
10            Concourse           Deli / Bodega              Grocery Store   
11    Concourse Village           Deli / Bodega             Sandwich Place   
12         Country Club          Sandwich Place                 Playground   
13         East Tremont             Pizza Place        Fried Chicken Joint   
14          Eastchester             Bus Station       Caribbean Restaurant   
15             Edenwald             Fish Market                Pizza Place   
16       Edgewater Park      Italian Restaurant              Deli / Bodega   
17            Fieldston             Bus Station                      River   
18              Fordham       Mobile Phone Shop                       Bank   
19         High  Bridge                Pharmacy                Pizza Place   
20          Hunts Point                    Bank             Waste Facility   
21          Kingsbridge             Pizza Place         Mexican Restaurant   
22  Kingsbridge Heights             Pizza Place                Coffee Shop   
23             Longwood           Grocery Store                  Wine Shop   
24              Melrose             Pizza Place                   Pharmacy   
25       Morris Heights                   Plaza  Latin American Restaurant   
26          Morris Park             Pizza Place              Deli / Bodega   
27           Morrisania          Discount Store                Bus Station   
28           Mott Haven              Donut Shop                Pizza Place   
29           Mount Eden                Pharmacy                Pizza Place   
30           Mount Hope           Grocery Store                Supermarket   
31      North Riverdale             Pizza Place                       Bank   
32              Norwood             Pizza Place                       Park   
33            Olinville    Caribbean Restaurant              Deli / Bodega   
34          Parkchester             Supermarket                Pizza Place   
35           Pelham Bay                    Bank         Italian Restaurant   
36       Pelham Gardens              Donut Shop                   Pharmacy   
37       Pelham Parkway             Pizza Place         Italian Restaurant   
38          Port Morris  Furniture / Home Store                 Donut Shop   
39            Riverdale    Medical Supply Store                       Park   
40        Schuylerville             Pizza Place                      Diner   
41            Soundview      Chinese Restaurant                   Bus Stop   
42       Spuyten Duyvil             Pizza Place                       Park   
43          Throgs Neck           Deli / Bodega                        Bar   
44            Unionport              Donut Shop             Ice Cream Shop   
45   University Heights             Pizza Place             Cosmetics Shop   
46             Van Nest             Pizza Place              Deli / Bodega   
47            Wakefield                Pharmacy             Ice Cream Shop   
48           West Farms             Bus Station              Metro Station   
49   Westchester Square    Fast Food Restaurant                   Pharmacy   
50       Williamsbridge    Caribb

In [56]:
queens_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
queens_data.head()

Borough     Neighborhood   Latitude  Longitude
0  Queens          Astoria  40.768509 -73.915654
1  Queens         Woodside  40.746349 -73.901842
2  Queens  Jackson Heights  40.751981 -73.882821
3  Queens         Elmhurst  40.744049 -73.881656
4  Queens     Howard Beach  40.654225 -73.838138

## Then Queens

In [57]:
address = 'Queens, NY'

geolocator3 = Nominatim(user_agent="ny_explorer")
location3 = geolocator3.geocode(address)
latitude3 = location.latitude
longitude3 = location.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(latitude3, longitude3))

The geograpical coordinate of Queens are 40.7896239, -73.9598939.


In [58]:
queens_venues = getNearbyVenues(names=queens_data['Neighborhood'],
                                   latitudes=queens_data['Latitude'],
                                   longitudes=queens_data['Longitude']
                                  )

Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
Corona
Forest Hills
Kew Gardens
Richmond Hill
Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Rego Park
Woodhaven
Ozone Park
South Ozone Park
College Point
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Hollis
South Jamaica
St. Albans
Rochdale
Springfield Gardens
Cambria Heights
Rosedale
Far Rockaway
Broad Channel
Breezy Point
Steinway
Beechhurst
Bay Terrace
Edgemere
Arverne
Rockaway Beach
Neponsit
Murray Hill
Floral Park
Holliswood
Jamaica Estates
Queensboro Hill
Hillcrest
Ravenswood
Lindenwood
Laurelton
Lefrak City
Belle Harbor
Rockaway Park
Somerville
Brookville
Bellaire
North Corona
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Middle Village
Malba
Hammels
Bayswater
Queensbridge


In [59]:
# one hot encoding
queens_onehot = pd.get_dummies(queens_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
queens_onehot['Neighborhood'] = queens_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [queens_onehot.columns[-1]] + list(queens_onehot.columns[:-1])
queens_onehot = queens_onehot[fixed_columns]

queens_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport Terminal  \
0            0                  0                  0                 0   
1            0                  0                  0                 0   
2            0                  0                  0                 0   
3            0                  0                  0                 0   
4            0                  0                  0                 0   

   American Restaurant  Antique Shop  Arepa Restaurant  \
0                    0             0                 0   
1                    0             0                 0   
2                    0             0                 0   
3                    0             0                 0   
4                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Automotive Shop  BBQ Joint  \
0                 0                   0                0          0   
1                 0                   0                0          0   
2                 0                   0                0          0   
3                 0                   0                0          0   
4                 0                   0                0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Garden  Bistro  \
0           0      0          0                0            0       0   
1           0      0          0                0            0       0   
2           0      0          0                0            0       0   
3           0      0          0                0            0       0   
4           0      0          0                0            0       0   

   Board Shop  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0           0          0         0              0                     1   
1           0          0         0              0                     0   
2           0          0         0              0                     0   
3           0          0         0              0                     0   
4           0          0         0              0                     0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Buffet  Building  Burger Joint  \
0               0        0                0       0         0             0   
1               0        0                0       0         0             0   
2               0        0                0       0         0             0   
3               0        0                0       0         0             0   
4               0        0                0       0         0             0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Business Service  Butcher  \
0              0         0            0         0                 0        0   
1              0         0            0         0                 0        0   
2              0         0            0         0                 0        0   
3              0         0            0         0                 0        0   
4              0         0            0         0                 0        0   

   Café  Cajun / Creole Restaurant  Candy Store  Cantonese Resta

In [60]:
queens_grouped = queens_onehot.groupby('Neighborhood').mean().reset_index()
queens_grouped.head()

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0          Arverne          0.0           0.000000                0.0   
1          Astoria          0.0           0.000000                0.0   
2  Astoria Heights          0.0           0.000000                0.0   
3       Auburndale          0.0           0.000000                0.0   
4      Bay Terrace          0.0           0.026316                0.0   

   Airport Terminal  American Restaurant  Antique Shop  Arepa Restaurant  \
0               0.0             0.000000           0.0               0.0   
1               0.0             0.020000           0.0               0.0   
2               0.0             0.000000           0.0               0.0   
3               0.0             0.058824           0.0               0.0   
4               0.0             0.052632           0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Asian Restaurant  Athletics & Sports  Automotive Shop  BBQ Joint  \
0               0.0            0.000000              0.0       0.00   
1               0.0            0.000000              0.0       0.02   
2               0.0            0.000000              0.0       0.00   
3               0.0            0.058824              0.0       0.00   
4               0.0            0.000000              0.0       0.00   

   Bagel Shop    Bakery      Bank       Bar  Baseball Field  Basketball Court  \
0        0.00  0.000000  0.000000  0.000000             0.0               0.0   
1        0.02  0.040000  0.000000  0.080000             0.0               0.0   
2        0.00  0.083333  0.000000  0.000000             0.0               0.0   
3        0.00  0.000000  0.000000  0.058824             0.0               0.0   
4        0.00  0.026316  0.026316  0.000000             0.0               0.0   

   Bath House     Beach  Beach Bar  Bed & Breakfast  Beer Garden  Bistro  \
0         0.0  0.055556        0.0         0.055556         0.00     0.0   
1         0.0  0.000000        0.0         0.000000         0.02     0.0   
2         0.0  0.000000        0.0         0.000000         0.00     0.0   
3         0.0  0.000000        0.0         0.000000         0.00     0.0   
4         0.0  0.000000        0.0         0.000000         0.00     0.0   

   Board Shop  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0    0.055556        0.0       0.0       0.000000                  0.00   
1    0.000000        0.0       0.0       0.000000                  0.02   
2    0.000000        0.0       0.0       0.083333                  0.00   
3    0.000000        0.0       0.0       0.000000                  0.00   
4    0.000000        0.0       0.0       0.000000                  0.00   

   Breakfast Spot  Brewery  Bubble Tea Shop  Buffet  Building  Burger Joint  \
0             0.0      0.0             0.00     0.0       0.0      0.000000   
1             0.0      0.0             0.02     0.0       0.0      0.000000   
2             0.0      0.0             0.00     0.0       0.0      0.083333   
3             0.0      0.0             0.00     0.0       0.0      0.000000   
4             0.0      0.0             0.00     0.0       0.0      0.000000   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Business Service  Butcher  \
0            0.0       0.0     0.000000  0.055556               0.0      0.0   
1            0.0       0.0     0.000000  0.000000               0.0      0.0   
2            0.0       0.0     0.083333  0.000000               0.0      0.0   
3            0.0       0.0     0.000000  0

In [61]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = queens_grouped['Neighborhood']

for ind in np.arange(queens_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(queens_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Arverne             Surf Spot        Sandwich Place   
1          Astoria                   Bar    Seafood Restaurant   
2  Astoria Heights            Playground    Italian Restaurant   
3       Auburndale  Fast Food Restaurant        Discount Store   
4      Bay Terrace        Clothing Store            Shoe Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Metro Station              Bus Stop                 Beach   
1     Indian Restaurant          Gourmet Shop          Dessert Shop   
2          Burger Joint                 Plaza         Bowling Alley   
3           Supermarket    Italian Restaurant      Toy / Game Store   
4         Women's Store   American Restaurant            Kids Store   

  6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
0       Bed & Breakfast                Donut Shop           Coffee Shop   
1                Bakery  Mediterranean Restaurant                   Gym   
2           Bus Station               Supermarket                Bakery   
3    Athletics & Sports                       Bar                 Train   
4        Lingerie Store         Mobile Phone Shop            Donut Shop   

  9th Most Common Venue     10th Most Common Venue  
0            Board Shop            Thai Restaurant  
1        Ice Cream Shop  Middle Eastern Restaurant  
2                  Food                Pizza Place  
3     Korean Restaurant               Noodle House  
4        Cosmetics Shop                Coffee Shop

## And Finally Staten Island

In [62]:
si_data = neighborhoods[neighborhoods['Borough'] == 'Staten Island'].reset_index(drop=True)
si_data.head()

Borough   Neighborhood   Latitude  Longitude
0  Staten Island     St. George  40.644982 -74.079353
1  Staten Island   New Brighton  40.640615 -74.087017
2  Staten Island      Stapleton  40.626928 -74.077902
3  Staten Island       Rosebank  40.615305 -74.069805
4  Staten Island  West Brighton  40.631879 -74.107182

In [63]:
address = 'Staten Island, NY'

geolocator4 = Nominatim(user_agent="ny_explorer")
location4 = geolocator4.geocode(address)
latitude4 = location.latitude
longitude4 = location.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(latitude4, longitude4))

The geograpical coordinate of Queens are 40.7896239, -73.9598939.


In [64]:
si_venues = getNearbyVenues(names=si_data['Neighborhood'],
                                   latitudes=si_data['Latitude'],
                                   longitudes=si_data['Longitude']
                                  )

St. George
New Brighton
Stapleton
Rosebank
West Brighton
Grymes Hill
Todt Hill
South Beach
Port Richmond
Mariner's Harbor
Port Ivory
Castleton Corners
New Springville
Travis
New Dorp
Oakwood
Great Kills
Eltingville
Annadale
Woodrow
Tottenville
Tompkinsville
Silver Lake
Sunnyside
Park Hill
Westerleigh
Graniteville
Arlington
Arrochar
Grasmere
Old Town
Dongan Hills
Midland Beach
Grant City
New Dorp Beach
Bay Terrace
Huguenot
Pleasant Plains
Butler Manor
Charleston
Rossville
Arden Heights
Greenridge
Heartland Village
Chelsea
Bloomfield
Bulls Head
Richmond Town
Shore Acres
Clifton
Concord
Emerson Hill
Randall Manor
Howland Hook
Elm Park
Manor Heights
Willowbrook
Sandy Ground
Egbertville
Prince's Bay
Lighthouse Hill
Richmond Valley
Fox Hills


In [65]:
# one hot encoding
si_onehot = pd.get_dummies(si_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
si_onehot['Neighborhood'] = si_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [si_onehot.columns[-1]] + list(si_onehot.columns[:-1])
si_onehot = si_onehot[fixed_columns]

si_onehot.head()

Neighborhood  Accessories Store  American Restaurant  Arcade  Art Museum  \
0   St. George                  0                    0       0           0   
1   St. George                  0                    0       0           0   
2   St. George                  0                    0       0           0   
3   St. George                  0                    0       0           0   
4   St. George                  0                    0       0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                    0                 0                   0          0   
1                    0                 0                   0          0   
2                    0                 0                   0          0   
3                    0                 0                   0          0   
4                    0                 0                   0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 1   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Beach  Beer Bar  Big Box Store  Board Shop  \
0                 0      0         0              0           0   
1                 0      0         0              0           0   
2                 0      0         0              0           0   
3                 0      0         0              0           0   
4                 0      0         0              0           0   

   Boat or Ferry  Bookstore  Bowling Alley  Breakfast Spot  Brewery  \
0              0          0              0               0        0   
1              0          0              0               0        0   
2              0          0              0               0        0   
3              0          0              0               0        0   
4              0          0              0               0        0   

   Bridal Shop  Burger Joint  Bus Stop  Café  Cajun / Creole Restaurant  \
0            0             0         0     0                          0   
1            0             0         0     0                          0   
2            0             0         0     0                          0   
3            0             0         0     0                          0   
4            0             0         0     0                          0   

   Campground  Caribbean Restaurant  Check Cashing Service  \
0           0                     0                      0   
1           0                     0                      0   
2           0                     0                      0   
3           0                     0                      0   
4           0                     0                      0   

   Chinese Restaurant  Clothing Store  Coffee Shop  Comedy Club  Concert Hall  \
0                   0               0            0            0             0   
1                   0               0            0            0             0   
2                   0               0            0            0             0   
3                   0               0            0            0             0   
4                   0               0            0            0             0   

   Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0                           0                  0               0   
1                           0                  0               0   
2                           0                  0               0   
3                           0                  0               0   
4                           0                  0               0   

   Cycle Studio  Dance Studio  Deli / Bodega  Department Store  Dessert Shop  \
0             0             0  

In [66]:
#frequency of attractions in staten island
si_grouped = si_onehot.groupby('Neighborhood').mean().reset_index()
si_grouped.head()

Neighborhood  Accessories Store  American Restaurant  Arcade  Art Museum  \
0       Annadale                0.0             0.083333     0.0         0.0   
1  Arden Heights                0.0             0.000000     0.0         0.0   
2      Arlington                0.0             0.000000     0.0         0.0   
3       Arrochar                0.0             0.000000     0.0         0.0   
4    Bay Terrace                0.0             0.000000     0.0         0.0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                  0.0               0.0            0.000000        0.0   
1                  0.0               0.0            0.000000        0.0   
2                  0.0               0.0            0.000000        0.0   
3                  0.0               0.0            0.045455        0.0   
4                  0.0               0.0            0.000000        0.0   

   Bagel Shop    Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0    0.000000  0.083333   0.0  0.0             0.0               0.0   
1    0.000000  0.000000   0.0  0.0             0.0               0.0   
2    0.000000  0.000000   0.0  0.0             0.0               0.0   
3    0.090909  0.000000   0.0  0.0             0.0               0.0   
4    0.000000  0.000000   0.0  0.0             0.0               0.0   

   Basketball Court  Beach  Beer Bar  Big Box Store  Board Shop  \
0               0.0    0.0       0.0            0.0         0.0   
1               0.0    0.0       0.0            0.0         0.0   
2               0.0    0.0       0.0            0.0         0.0   
3               0.0    0.0       0.0            0.0         0.0   
4               0.0    0.0       0.0            0.0         0.0   

   Boat or Ferry  Bookstore  Bowling Alley  Breakfast Spot  Brewery  \
0            0.0        0.0            0.0             0.0      0.0   
1            0.0        0.0            0.0             0.0      0.0   
2            0.0        0.0            0.0             0.0      0.0   
3            0.0        0.0            0.0             0.0      0.0   
4            0.0        0.0            0.0             0.0      0.0   

   Bridal Shop  Burger Joint  Bus Stop  Café  Cajun / Creole Restaurant  \
0          0.0           0.0  0.000000   0.0                        0.0   
1          0.0           0.0  0.166667   0.0                        0.0   
2          0.0           0.0  0.333333   0.0                        0.0   
3          0.0           0.0  0.090909   0.0                        0.0   
4          0.0           0.0  0.000000   0.0                        0.0   

   Campground  Caribbean Restaurant  Check Cashing Service  \
0         0.0                   0.0                    0.0   
1         0.0                   0.0                    0.0   
2         0.0                   0.0                    0.0   
3         0.0                   0.0                    0.0   
4         0.0                   0.0                    0.0   

   Chinese Restaurant  Clothing Store  Coffee Shop  Comedy Club  Concert Hall  \
0                 0.0             0.0     0.000000          0.0           0.0   
1                 0.0             0.0     0.166667          0.0           0.0   
2                 0.0             0.0     0.166667          0.0           0.0   
3                 0.0             0.0     0.000000          0.0           0.0   
4                 0.0             0.0     0.000000          0.0           0.0   

   Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0                         0.0                0.0        0.000000   
1                         0.0                0.0        0.000000   
2                         0.0                0.0        0.000000   
3                         0.0                0.0        0.045455   
4                         0.0                0.0        0.000000   

   Cycle Studio  Dance Studio  Deli / Bodega  Department Store  Dessert Shop  \
0        

In [67]:
#frequency of attractions in manhattan
manhattan_grouped.head()

Neighborhood  Accessories Store  Adult Boutique  African Restaurant  \
0  Battery Park City                0.0             0.0            0.000000   
1      Carnegie Hill                0.0             0.0            0.000000   
2     Central Harlem                0.0             0.0            0.044444   
3            Chelsea                0.0             0.0            0.000000   
4          Chinatown                0.0             0.0            0.000000   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0             0.000000           0.0     0.0               0.0   
1             0.020000           0.0     0.0               0.0   
2             0.044444           0.0     0.0               0.0   
3             0.040000           0.0     0.0               0.0   
4             0.060000           0.0     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0     0.000000        0.00                  0.0   
1                     0.0     0.000000        0.02                  0.0   
2                     0.0     0.022222        0.00                  0.0   
3                     0.0     0.020000        0.00                  0.0   
4                     0.0     0.000000        0.00                  0.0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0              0.00                0.02        0.02                    0.0   
1              0.00                0.00        0.00                    0.0   
2              0.00                0.00        0.00                    0.0   
3              0.00                0.00        0.00                    0.0   
4              0.04                0.00        0.00                    0.0   

   Austrian Restaurant  BBQ Joint  Baby Store  Bagel Shop    Bakery  Bank  \
0                  0.0   0.000000         0.0    0.000000  0.000000   0.0   
1                  0.0   0.000000         0.0    0.020000  0.020000   0.0   
2                  0.0   0.022222         0.0    0.022222  0.022222   0.0   
3                  0.0   0.000000         0.0    0.000000  0.040000   0.0   
4                  0.0   0.000000         0.0    0.000000  0.020000   0.0   

        Bar  Baseball Field  Beer Bar  Beer Garden  Beer Store  \
0  0.000000             0.0  0.000000          0.0         0.0   
1  0.020000             0.0  0.000000          0.0         0.0   
2  0.044444             0.0  0.022222          0.0         0.0   
3  0.000000             0.0  0.020000          0.0         0.0   
4  0.000000             0.0  0.000000          0.0         0.0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                       0.0       0.00         0.0    0.02         0.0   
1                       0.0       0.00         0.0    0.00         0.0   
2                       0.0       0.00         0.0    0.00         0.0   
3                       0.0       0.00         0.0    0.00         0.0   
4                       0.0       0.02         0.0    0.00         0.0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Breakfast Spot  \
0            0.0   0.000000  0.000000         0.0             0.0   
1            0.0   0.060000  0.000000         0.0             0.0   
2            0.0   0.022222  0.022222         0.0             0.0   
3            0.0   0.040000  0.000000         0.0             0.0   
4            0.0   0.000000  0.040000         0.0             0.0   

   Bridal Shop  Bridge  Bubble Tea Shop  Building  Burger Joint  \
0          0.0     0.0             0.00      0.02          0.04   
1          0.0     0.0             0.00      0.00          0.02   
2          0.0     0.0             0.00      0.00          0.00   
3          0.0     0.0             0.00      0.00          0.00   
4          0.0     0.0             0.02      0.00          0.00   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Butcher  Cafeteria  \
0            0.0    

In [68]:
#frequency of attractions in brooklyn
brooklyn_grouped.head()

Neighborhood  Yoga Studio  Accessories Store  Airport Terminal  \
0          Bath Beach          0.0                0.0               0.0   
1           Bay Ridge          0.0                0.0               0.0   
2  Bedford Stuyvesant          0.0                0.0               0.0   
3         Bensonhurst          0.0                0.0               0.0   
4        Bergen Beach          0.0                0.0               0.0   

   American Restaurant  Antique Shop  Arepa Restaurant  \
0             0.000000           0.0               0.0   
1             0.040000           0.0               0.0   
2             0.000000           0.0               0.0   
3             0.030303           0.0               0.0   
4             0.000000           0.0               0.0   

   Argentinian Restaurant  Art Gallery  Arts & Crafts Store  \
0                     0.0          0.0                  0.0   
1                     0.0          0.0                  0.0   
2                     0.0          0.0                  0.0   
3                     0.0          0.0                  0.0   
4                     0.0          0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                   0.0          0.023810            0.000000          0.0   
1                   0.0          0.000000            0.000000          0.0   
2                   0.0          0.000000            0.000000          0.0   
3                   0.0          0.030303            0.000000          0.0   
4                   0.0          0.000000            0.166667          0.0   

   BBQ Joint  Bagel Shop    Bakery     Bank       Bar  Baseball Field  \
0   0.000000    0.000000  0.023810  0.02381  0.000000        0.000000   
1   0.000000    0.040000  0.000000  0.00000  0.020000        0.000000   
2   0.035714    0.035714  0.000000  0.00000  0.071429        0.000000   
3   0.000000    0.030303  0.030303  0.00000  0.030303        0.000000   
4   0.000000    0.000000  0.000000  0.00000  0.000000        0.166667   

   Baseball Stadium  Basketball Court  Beach  Beer Bar  Beer Garden  \
0               0.0               0.0    0.0       0.0          0.0   
1               0.0               0.0    0.0       0.0          0.0   
2               0.0               0.0    0.0       0.0          0.0   
3               0.0               0.0    0.0       0.0          0.0   
4               0.0               0.0    0.0       0.0          0.0   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Shop  Board Shop  \
0         0.0            0.0                       0.0        0.0         0.0   
1         0.0            0.0                       0.0        0.0         0.0   
2         0.0            0.0                       0.0        0.0         0.0   
3         0.0            0.0                       0.0        0.0         0.0   
4         0.0            0.0                       0.0        0.0         0.0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Breakfast Spot  Brewery  \
0            0.0       0.00  0.000000         0.0            0.00      0.0   
1            0.0       0.02  0.000000         0.0            0.02      0.0   
2            0.0       0.00  0.035714         0.0            0.00      0.0   
3            0.0       0.00  0.000000         0.0            0.00      0.0   
4            0.0       0.00  0.000000         0.0            0.00      0.0   

   Bridal Shop  Bridge  Bubble Tea Shop  Buffet  Burger Joint  Burrito Place  \
0     0.000000     0.0         0.047619     0.0       0.02381            0.0   
1     0.000000     0.0         0.000000     0.0       0.00000            0.0   
2     0.000000     0.0         0.000000     0.0       0.00000            0.0   
3     0.030303     0.0         0.000000     0.0       0.00000            0.0   
4     0.000000     0.0         0.000000     0.0       0.00000            0.0   

   Bus Line  Bus Station  Bus Stop  Business Service   But

In [69]:
#frequency of attractions in queens
queens_grouped.head()

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0          Arverne          0.0           0.000000                0.0   
1          Astoria          0.0           0.000000                0.0   
2  Astoria Heights          0.0           0.000000                0.0   
3       Auburndale          0.0           0.000000                0.0   
4      Bay Terrace          0.0           0.026316                0.0   

   Airport Terminal  American Restaurant  Antique Shop  Arepa Restaurant  \
0               0.0             0.000000           0.0               0.0   
1               0.0             0.020000           0.0               0.0   
2               0.0             0.000000           0.0               0.0   
3               0.0             0.058824           0.0               0.0   
4               0.0             0.052632           0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Asian Restaurant  Athletics & Sports  Automotive Shop  BBQ Joint  \
0               0.0            0.000000              0.0       0.00   
1               0.0            0.000000              0.0       0.02   
2               0.0            0.000000              0.0       0.00   
3               0.0            0.058824              0.0       0.00   
4               0.0            0.000000              0.0       0.00   

   Bagel Shop    Bakery      Bank       Bar  Baseball Field  Basketball Court  \
0        0.00  0.000000  0.000000  0.000000             0.0               0.0   
1        0.02  0.040000  0.000000  0.080000             0.0               0.0   
2        0.00  0.083333  0.000000  0.000000             0.0               0.0   
3        0.00  0.000000  0.000000  0.058824             0.0               0.0   
4        0.00  0.026316  0.026316  0.000000             0.0               0.0   

   Bath House     Beach  Beach Bar  Bed & Breakfast  Beer Garden  Bistro  \
0         0.0  0.055556        0.0         0.055556         0.00     0.0   
1         0.0  0.000000        0.0         0.000000         0.02     0.0   
2         0.0  0.000000        0.0         0.000000         0.00     0.0   
3         0.0  0.000000        0.0         0.000000         0.00     0.0   
4         0.0  0.000000        0.0         0.000000         0.00     0.0   

   Board Shop  Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  \
0    0.055556        0.0       0.0       0.000000                  0.00   
1    0.000000        0.0       0.0       0.000000                  0.02   
2    0.000000        0.0       0.0       0.083333                  0.00   
3    0.000000        0.0       0.0       0.000000                  0.00   
4    0.000000        0.0       0.0       0.000000                  0.00   

   Breakfast Spot  Brewery  Bubble Tea Shop  Buffet  Building  Burger Joint  \
0             0.0      0.0             0.00     0.0       0.0      0.000000   
1             0.0      0.0             0.02     0.0       0.0      0.000000   
2             0.0      0.0             0.00     0.0       0.0      0.083333   
3             0.0      0.0             0.00     0.0       0.0      0.000000   
4             0.0      0.0             0.00     0.0       0.0      0.000000   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Business Service  Butcher  \
0            0.0       0.0     0.000000  0.055556               0.0      0.0   
1            0.0       0.0     0.000000  0.000000               0.0      0.0   
2            0.0       0.0     0.083333  0.000000               0.0      0.0   
3            0.0       0.0     0.000000  0

In [71]:
bronx_grouped.head()

Neighborhood  Accessories Store  African Restaurant  American Restaurant  \
0      Allerton                0.0                 0.0              0.03125   
1    Baychester                0.0                 0.0              0.00000   
2  Bedford Park                0.0                 0.0              0.00000   
3       Belmont                0.0                 0.0              0.02000   
4     Bronxdale                0.0                 0.0              0.00000   

     Arcade  Arepa Restaurant  Art Gallery  Art Museum  Asian Restaurant  \
0  0.000000               0.0          0.0         0.0               0.0   
1  0.047619               0.0          0.0         0.0               0.0   
2  0.000000               0.0          0.0         0.0               0.0   
3  0.000000               0.0          0.0         0.0               0.0   
4  0.000000               0.0          0.0         0.0               0.0   

   BBQ Joint  Bagel Shop  Bakery      Bank      Bar  Baseball Field  \
0        0.0         0.0    0.00  0.000000  0.00000         0.00000   
1        0.0         0.0    0.00  0.047619  0.00000         0.00000   
2        0.0         0.0    0.00  0.000000  0.03125         0.03125   
3        0.0         0.0    0.08  0.000000  0.02000         0.00000   
4        0.0         0.0    0.00  0.083333  0.00000         0.00000   

   Basketball Court  Beer Bar  Boat or Ferry  Bookstore  Bowling Alley  \
0               0.0       0.0            0.0        0.0            0.0   
1               0.0       0.0            0.0        0.0            0.0   
2               0.0       0.0            0.0        0.0            0.0   
3               0.0       0.0            0.0        0.0            0.0   
4               0.0       0.0            0.0        0.0            0.0   

   Breakfast Spot  Brewery  Buffet  Building  Burger Joint  Bus Line  \
0        0.031250      0.0     0.0       0.0       0.00000       0.0   
1        0.000000      0.0     0.0       0.0       0.00000       0.0   
2        0.000000      0.0     0.0       0.0       0.03125       0.0   
3        0.000000      0.0     0.0       0.0       0.00000       0.0   
4        0.083333      0.0     0.0       0.0       0.00000       0.0   

   Bus Station  Bus Stop  Café  Candy Store  Caribbean Restaurant  \
0      0.06250       0.0   0.0          0.0                   0.0   
1      0.00000       0.0   0.0          0.0                   0.0   
2      0.03125       0.0   0.0          0.0                   0.0   
3      0.00000       0.0   0.0          0.0                   0.0   
4      0.00000       0.0   0.0          0.0                   0.0   

   Check Cashing Service  Cheese Shop  Chinese Restaurant  Clothing Store  \
0                    0.0         0.00            0.062500             0.0   
1                    0.0         0.00            0.000000             0.0   
2                    0.0         0.00            0.062500             0.0   
3                    0.0         0.02            0.000000             0.0   
4                    0.0         0.00            0.083333             0.0   

   Coffee Shop  Comfort Food Restaurant  Construction & Landscaping  \
0      0.00000                      0.0                         0.0   
1      0.00000                      0.0                         0.0   
2      0.03125                      0.0                         0.0   
3      0.02000                      0.0                         0.0   
4      0.00000                      0.0                         0.0   

   Convenience Store  Cosmetics Shop  Cupcake Shop  Dance Studio  \
0           0.000000          0.0625           0.0           0.0   
1           0.047619          0.0000           0.0           0.0   
2           0.000000          0.0000           0.0           0.0   
3           0.000000          0.0000           0.0           0.0   
4           0.000000          0.0000           0.0           0.0   

   Deli / Bodega  Department Store  Dessert Shop  Di

In [72]:
#group all dataframes containing frequencies of established attractions into one dataframe
nygrouping = si_grouped + manhattan_grouped + bronx_grouped + brooklyn_grouped + queens_grouped

In [73]:
nygrouping

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0            0.000000             NaN                NaN                 NaN   
1            0.000000             NaN                NaN                 NaN   
2            0.000000             NaN                NaN                 NaN   
3            0.000000             NaN                NaN                 NaN   
4            0.026316             NaN                NaN                 NaN   
5            0.000000             NaN                NaN                 NaN   
6            0.000000             NaN                NaN                 NaN   
7            0.000000             NaN                NaN                 NaN   
8            0.000000             NaN                NaN                 NaN   
9            0.000000             NaN                NaN                 NaN   
10           0.000000             NaN                NaN                 NaN   
11           0.000000             NaN                NaN                 NaN   
12           0.000000             NaN                NaN                 NaN   
13           0.000000             NaN                NaN                 NaN   
14           0.000000             NaN                NaN                 NaN   
15           0.000000             NaN                NaN                 NaN   
16           0.000000             NaN                NaN                 NaN   
17           0.000000             NaN                NaN                 NaN   
18           0.020000             NaN                NaN                 NaN   
19           0.000000             NaN                NaN                 NaN   
20           0.000000             NaN                NaN                 NaN   
21           0.000000             NaN                NaN                 NaN   
22           0.000000             NaN                NaN                 NaN   
23           0.000000             NaN                NaN                 NaN   
24           0.090909             NaN                NaN                 NaN   
25           0.000000             NaN                NaN                 NaN   
26           0.000000             NaN                NaN                 NaN   
27           0.000000             NaN                NaN                 NaN   
28           0.000000             NaN                NaN                 NaN   
29           0.000000             NaN                NaN                 NaN   
30           0.000000             NaN                NaN                 NaN   
31           0.000000             NaN                NaN                 NaN   
32           0.000000             NaN                NaN                 NaN   
33           0.038462             NaN                NaN                 NaN   
34           0.000000             NaN                NaN                 NaN   
35           0.000000             NaN                NaN                 NaN   
36           0.000000             NaN                NaN                 NaN   
37           0.020000             NaN                NaN                 NaN   
38           0.000000             NaN                NaN                 NaN   
39           0.000000             NaN                NaN                 NaN   
40                NaN             NaN                NaN                 NaN   
41                NaN             NaN                NaN                 NaN   
42                NaN             NaN                NaN                 NaN   
43                NaN             NaN                NaN                 NaN   
44                NaN             NaN                NaN                 NaN   
45                NaN             NaN                NaN                 NaN   
46                NaN             NaN                NaN                 NaN   
47                NaN             NaN                NaN                 NaN   
48                NaN             NaN                NaN                 NaN   
49  

In [76]:
#drop every column aside from the frequency of Mexican Restaurant and Neighborhood
nygrouping.drop(nygrouping.columns.difference(['Mexican Restaurant','Neighborhood']), 1, inplace=True)
nysolution = nygrouping
nysolution.dropna()

Mexican Restaurant                                       Neighborhood
0             0.020000  AnnadaleBattery Park CityAllertonBath BeachArv...
1             0.087619  Arden HeightsCarnegie HillBaychesterBay RidgeA...
2             0.062500  ArlingtonCentral HarlemBedford ParkBedford Stu...
3             0.020000        ArrocharChelseaBelmontBensonhurstAuburndale
4             0.083333  Bay TerraceChinatownBronxdaleBergen BeachBay T...
5             0.040000  BloomfieldCivic CenterCastle HillBoerum HillBa...
6             0.000000  Bulls HeadClintonCity IslandBorough ParkBayswater
7             0.139535  Butler ManorEast HarlemClaremont VillageBright...
8             0.040000  Castleton CornersEast VillageClason PointBroad...
9             0.098824  CharlestonFinancial DistrictCo-op CityBrooklyn...
10            0.000000       ChelseaFlatironConcourseBrownsvilleBellerose
11            0.223914  CliftonGramercyConcourse VillageBushwickBlissv...
12            0.000000  ConcordGreenwich VillageCountry ClubCanarsieBr...
13            0.160000  Dongan HillsHamilton HeightsEast TremontCarrol...
14            0.027027  EgbertvilleHudson YardsEastchesterCity LineBro...
15            0.120000       Elm ParkInwoodEdenwaldClinton HillBrookville
16            0.020000  EltingvilleLenox HillEdgewater ParkCobble Hill...
17            0.000000  Fox HillsLincoln SquareFieldstonConey IslandCo...
18            0.117647  GranitevilleLittle ItalyFordhamCrown HeightsCo...
19            0.102665  Grant CityLower East SideHigh  BridgeCypress H...
20            0.052668  GrasmereManhattan ValleyHunts PointDitmas Park...
21            0.122553  Great KillsManhattanvilleKingsbridgeDowntownEd...
22            0.228754  GreenridgeMarble HillKingsbridge HeightsDumboE...
23            0.000000  Grymes HillMidtownLongwoodDyker HeightsFar Roc...
24            0.035714  Heartland VillageMidtown SouthMelroseEast Flat...
25            0.025641  HuguenotMorningside HeightsMorris HeightsEast ...
26            0.020000  Lighthouse HillMurray HillMorris ParkEast Will...
27            0.080952  Manor HeightsNohoMorrisaniaErasmusForest Hills...
28            0.111111  Mariner's HarborRoosevelt IslandMott HavenFlat...
29            0.047619      Midland BeachSohoMount EdenFlatlandsGlen Oaks
30            0.000000  New BrightonStuyvesant TownMount HopeFort Gree...
31            0.127619  New DorpSutton PlaceNorth RiverdaleFort Hamilt...
32            0.050303  New Dorp BeachTribecaNorwoodFulton FerryHillcrest
33            0.202704  New SpringvilleTudor CityOlinvilleGeorgetownHo...
34            0.028571  OakwoodTurtle BayParkchesterGerritsen BeachHol...
35            0.093419  Old TownUpper East SidePelham BayGowanusHoward...
36            0.020000  Park HillUpper West SidePelham GardensGravesen...
37            0.060000  Pleasant PlainsWashington HeightsPelham Parkwa...
38            0.245455  Port RichmondWest VillagePort MorrisHighland P...
39            0.072632  Prince's BayYorkvilleRiverdaleHomecrestJamaica...

In [78]:
#Get full view of nbhd names
pd.set_option('display.max_colwidth', -1)
nysolution.dropna()

Mexican Restaurant  \
0   0.020000             
1   0.087619             
2   0.062500             
3   0.020000             
4   0.083333             
5   0.040000             
6   0.000000             
7   0.139535             
8   0.040000             
9   0.098824             
10  0.000000             
11  0.223914             
12  0.000000             
13  0.160000             
14  0.027027             
15  0.120000             
16  0.020000             
17  0.000000             
18  0.117647             
19  0.102665             
20  0.052668             
21  0.122553             
22  0.228754             
23  0.000000             
24  0.035714             
25  0.025641             
26  0.020000             
27  0.080952             
28  0.111111             
29  0.047619             
30  0.000000             
31  0.127619             
32  0.050303             
33  0.202704             
34  0.028571             
35  0.093419             
36  0.020000             
37  0.060000             
38  0.245455             
39  0.072632             

                                                                Neighborhood  
0   AnnadaleBattery Park CityAllertonBath BeachArverne                        
1   Arden HeightsCarnegie HillBaychesterBay RidgeAstoria                      
2   ArlingtonCentral HarlemBedford ParkBedford StuyvesantAstoria Heights      
3   ArrocharChelseaBelmontBensonhurstAuburndale                               
4   Bay TerraceChinatownBronxdaleBergen BeachBay Terrace                      
5   BloomfieldCivic CenterCastle HillBoerum HillBayside                       
6   Bulls HeadClintonCity IslandBorough ParkBayswater                         
7   Butler ManorEast HarlemClaremont VillageBrighton BeachBeechhurst          
8   Castleton CornersEast VillageClason PointBroadway JunctionBellaire        
9   CharlestonFinancial DistrictCo-op CityBrooklyn HeightsBelle Harbor        
10  ChelseaFlatironConcourseBrownsvilleBellerose                              
11  CliftonGramercyConcourse VillageBushwickBlissville                        
12  ConcordGreenwich VillageCountry ClubCanarsieBreezy Point                  
13  Dongan HillsHamilton HeightsEast TremontCarroll GardensBriarwood          
14  EgbertvilleHudson YardsEastchesterCity LineBroad Channel                  
15  Elm ParkInwoodEdenwaldClinton HillBrookville                              
16  EltingvilleLenox HillEdgewater ParkCobble HillCambria Heights             
17  Fox HillsLincoln SquareFieldstonConey IslandCollege Point                 
18  GranitevilleLittle ItalyFordhamCrown HeightsCorona                        
19  Grant CityLower East SideHigh  BridgeCypress HillsDouglaston              
20  GrasmereManhattan ValleyHunts PointDitmas ParkEast Elmhurst               
21  Great KillsManhattanvilleKingsbridgeDowntownEdgemere                      
22  GreenridgeMarble HillKingsbridge HeightsDumboElmhurst                     
23  Grymes HillMidtownLongwoodDyker HeightsFar Rockaway                       
24  Heartland VillageMidtown SouthMelroseEast FlatbushFloral Park             
25  HuguenotMorningside HeightsMorris HeightsEast New YorkFlushing            
26  Lighthouse HillMurray HillMorris ParkEast WilliamsburgForest Hills        
27  Manor HeightsNohoMorrisaniaErasmusForest Hills Gardens                    
28  Mariner's HarborRoosevelt IslandMott HavenFlatbushFresh Meadows           
29  Midland BeachSohoMount EdenFlatlandsGlen Oaks                             
30  New BrightonStuyvesant TownMount HopeFort GreeneGlendale                  
31  New DorpSutton PlaceNorth RiverdaleFort HamiltonHammels                   
32  New Dorp BeachTribecaNorwoodFulton FerryHillcrest                         
33  New SpringvilleTudor CityOlinvilleGeorgetownHollis                        
34  OakwoodTurtle BayParkchesterGerritsen BeachHolliswood                     
35  Old TownUpper East SidePelham BayGowanusHoward Beach                      
36  Park HillU

In [86]:
nysolution[nysolution['Mexican Restaurant']==0]

Mexican Restaurant  \
6   0.0                  
10  0.0                  
12  0.0                  
17  0.0                  
23  0.0                  
30  0.0                  

                                                 Neighborhood  
6   Bulls HeadClintonCity IslandBorough ParkBayswater          
10  ChelseaFlatironConcourseBrownsvilleBellerose               
12  ConcordGreenwich VillageCountry ClubCanarsieBreezy Point   
17  Fox HillsLincoln SquareFieldstonConey IslandCollege Point  
23  Grymes HillMidtownLongwoodDyker HeightsFar Rockaway        
30  New BrightonStuyvesant TownMount HopeFort GreeneGlendale

In [20]:
import pandas as pd
data = {'Neighborhood Name': ['Bulls Head', 'Clinton', 'City Island', 'Borough Park', 'Bayswater',
'Chelsea', 'Flatiron', 'Concourse', 'Brownsville', 'Bellerose',
'Concord', 'Greenwich Village', 'Counry Club', 'Canarsie', 'Breezy Point',
'Fox Hills', 'Lincoln Square', 'Fieldston', 'Coney Island', 'College Point',
'Grymes Hill', 'Midtown', 'Longwood', 'Dyker heights', 'Far Rockaway',
'New Brighton', 'Stuyvesant Town', 'Mount Hope', 'Fort Greene', 'Glendale'],
       'Population': [90761,1939,4434,106357,13695,47325,14380,75371,58300,1165,8494,30591,7953,83693,4079,32808,49957,3292,24711,35916,4984,104753,26196,42419,60035,5795,21049,6668,28335,32496]}

In [21]:
df = pd.DataFrame({ key:pd.Series(value) for key, value in data.items() })

In [22]:
df

Neighborhood Name  Population
0          Bulls Head       90761
1             Clinton        1939
2         City Island        4434
3        Borough Park      106357
4           Bayswater       13695
5             Chelsea       47325
6            Flatiron       14380
7           Concourse       75371
8         Brownsville       58300
9           Bellerose        1165
10            Concord        8494
11  Greenwich Village       30591
12        Counry Club        7953
13           Canarsie       83693
14       Breezy Point        4079
15          Fox Hills       32808
16     Lincoln Square       49957
17          Fieldston        3292
18       Coney Island       24711
19      College Point       35916
20        Grymes Hill        4984
21            Midtown      104753
22           Longwood       26196
23      Dyker heights       42419
24       Far Rockaway       60035
25       New Brighton        5795
26    Stuyvesant Town       21049
27         Mount Hope        6668
28        Fort Greene       28335
29           Glendale       32496

In [23]:
df.max()

Neighborhood Name    Stuyvesant Town
Population                    106357
dtype: object

Stuyvesant Town would be the ideal location to open up a Mexican Restaurant!